In [1]:
import gym
import gym_pendrogone

import numpy as np
import matplotlib.pyplot as plt
# %matplotlib inline

# Imports specifically so we can render outputs in Jupyter.
from JSAnimation.IPython_display import display_animation
from matplotlib import animation
from IPython.display import display
from IPython.display import HTML

# for auto-reloading external modules
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
# %load_ext autoreload
# %autoreload 2

from utils import *

def display_frames_as_gif(frames):
    """
    Displays a list of frames as a gif, with controls
    """
    #plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 72)
    patch = plt.imshow(frames[0])
    plt.axis('off')

    def animate(i):
        patch.set_data(frames[i])

    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=25)
    anim = HTML(anim.to_html5_video())
    # display(display_animation(anim, default_mode='loop'))

In [ ]:
env = gym.make('Pendrogone-v1')

print(env.observation_space.shape)
print(env.action_space.shape)

action = 0.55 * 9.81 / 2

In [ ]:
a = (action, action)

frames = []
obs = env.reset()

for _ in range(1):
    obs, r, done, _ = env.step(a)
    # print(obs)
    frames.append(env.render(mode = 'rgb_array'))
display_frames_as_gif(frames)

# SAC

In [2]:
import gym_pendrogone   
from stable_baselines3 import PPO, a2c, SAC 
from stable_baselines3.common.env_util import make_vec_env
import gym

In [3]:
env = gym.make("Pendrogone-v1")

model = SAC.load("Pendrogone_sac.bak")

#now make the time series
max_time = 60
dt = env.dt # useful for the animation function
freq = 1/dt       # frequency/Hz
t = np.linspace(0, max_time, int(freq*max_time+1))
d2r = np.pi/180

/Users/kevinlee/anaconda3/lib/python3.7/site-packages/gym/spaces/box.py:74: UserWarning: WARN: Box bound precision lowered by casting to float32
  "Box bound precision lowered by casting to {}".format(self.dtype)
/Users/kevinlee/anaconda3/lib/python3.7/site-packages/stable_baselines3/common/save_util.py:169: UserWarning: Could not deserialize object lr_schedule. Consider using `custom_objects` argument to replace this object.
  + "this object."


In [46]:
def setObjective(env, objective):
    d = objective - env.env.state[0:2]
    if np.linalg.norm(d) <= 2:
        env.env.objective = objective
    else:
        unit_d = d / np.linalg.norm(d)
        env.env.objective = env.env.state[0:2] + 2 * unit_d

obs_list, actions_list, rewards_list, obj_list = [], [], [], []

final_objective = np.array([5,8])

obs = env.reset()
env.env.state = np.array([0, 0, 2*np.pi, np.pi-30*d2r, 0, 0, 0, 0])
setObjective(env, final_objective)
obs_list.append(env.obs)
obj_list.append(env.objective)

for i in range(1, len(t)):
    action, _ = model.predict(obs)
    obs, rewards, dones, info = env.step(action)
    
    # Update objective
    setObjective(env, final_objective)
    
    # Add to lists
    obs_list.append(obs)
    actions_list.append(action)
    rewards_list.append(rewards)
    obj_list.append(env.objective)
    #env.render()

In [47]:
obs_np = np.array(obs_list)
obj_np = np.array(obj_list)
x = obs_np[:, 0] + obj_np[:, 0]
y = obs_np[:, 1] + obj_np[:, 1]
theta = np.arctan2(obs_np[:, 2], obs_np[:, 3])
phi = np.arctan2(obs_np[:, 4], obs_np[:, 5])

In [48]:
animate_planar_quad_with_inverted_pendulum(t, x, y, theta, phi, display_in_notebook=True)

# Circle Trajectory

In [49]:
obs_list, actions_list, rewards_list, obj_list = [], [], [], []

final_objective = np.array([5,8])

w = 2*np.pi/30
x_des = 2*np.cos(w*t)
y_des = 2*np.sin(w*t)

obs = env.reset()
env.env.state = np.array([0, 0, 2*np.pi, np.pi-30*d2r, 0, 0, 0, 0])
setObjective(env, np.array([x_des[0], y_des[0]]))
obs_list.append(env.obs)
obj_list.append(env.objective)

for i in range(1, len(t)):
    action, _ = model.predict(obs)
    obs, rewards, dones, info = env.step(action)
    
    # Update objective
    setObjective(env, np.array([x_des[i], y_des[i]]))
    
    # Add to lists
    obs_list.append(obs)
    actions_list.append(action)
    rewards_list.append(rewards)
    obj_list.append(env.objective)

In [50]:
obs_np = np.array(obs_list)
obj_np = np.array(obj_list)
x = obs_np[:, 0] + obj_np[:, 0]
y = obs_np[:, 1] + obj_np[:, 1]
theta = np.arctan2(obs_np[:, 2], obs_np[:, 3])
phi = np.arctan2(obs_np[:, 4], obs_np[:, 5])

In [51]:
animate_planar_quad_with_inverted_pendulum(t, x, y, theta, phi, display_in_notebook=True)